### **TUGAS BESAR IOT TEMP**

---

KELOMPOK        : 03

Kelas       : SI4703

---

In [35]:
import pandas as pd

df = pd.read_csv('IOT-temp.csv')

df.head()

id  room_id/id        noted_date  temp  \
0  __export__.temp_log_196134_bd201015  Room Admin  08-12-2018 09:30    29   
1  __export__.temp_log_196131_7bca51bc  Room Admin  08-12-2018 09:30    29   
2  __export__.temp_log_196127_522915e3  Room Admin  08-12-2018 09:29    41   
3  __export__.temp_log_196128_be0919cf  Room Admin  08-12-2018 09:29    41   
4  __export__.temp_log_196126_d30b72fb  Room Admin  08-12-2018 09:29    31   

  out/in  
0     In  
1     In  
2    Out  
3    Out  
4     In

In [36]:
print(df.describe(include='all'))

                                         id  room_id/id        noted_date  \
count                                 97606       97606             97606   
unique                                97605           1             27920   
top     __export__.temp_log_196108_4a983c7e  Room Admin  12-09-2018 03:09   
freq                                      2       97606                65   
mean                                    NaN         NaN               NaN   
std                                     NaN         NaN               NaN   
min                                     NaN         NaN               NaN   
25%                                     NaN         NaN               NaN   
50%                                     NaN         NaN               NaN   
75%                                     NaN         NaN               NaN   
max                                     NaN         NaN               NaN   

                temp out/in  
count   97606.000000  97606  
unique         

In [37]:
df.isnull().sum()

id            0
room_id/id    0
noted_date    0
temp          0
out/in        0
dtype: int64

In [38]:
import plotly.express as px

# Boxplot suhu berdasarkan out/in
fig = px.box(df, x='out/in', y='temp', title='Distribusi Suhu Berdasarkan Lokasi (In/Out)')
fig.show()

In [39]:
# Konversi noted_date ke datetime
df['noted_date'] = pd.to_datetime(df['noted_date'], format='%d-%m-%Y %H:%M')

# Scatter plot tren suhu
fig = px.scatter(df, x='noted_date', y='temp', color='out/in', title='Tren Suhu Seiring Waktu')
fig.show()

In [40]:
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN

# Preprocessing
df = df.drop_duplicates()
df['noted_date'] = pd.to_datetime(df['noted_date'], format='%d-%m-%Y %H:%M')
df['hour'] = df['noted_date'].dt.hour
df = df.drop(columns=['id', 'room_id/id'])
df['temp'] = df['temp'].fillna(df['temp'].mean())
df['out/in'] = df['out/in'].map({'In': 0, 'Out': 1}).fillna(0)
df['hour'] = df['hour'].fillna(df['hour'].mode()[0])
scaler = StandardScaler()
df['temp_scaled'] = scaler.fit_transform(df[['temp']])

# Fitur untuk clustering
features = df[['temp_scaled', 'out/in', 'hour']]

# DBSCAN
dbscan = DBSCAN(eps=0.5, min_samples=5)
df['cluster'] = dbscan.fit_predict(features)

# Distribusi cluster
print("Distribusi Cluster:")
print(df['cluster'].value_counts().sort_index())

Distribusi Cluster:
cluster
-1        9
 0     1584
 1     2805
 2     1266
 3      823
 4     1026
 5     1384
 6      770
 7     2047
 8     3203
 9      880
 10    2008
 11     682
 12     890
 13    2791
 14     718
 15    2876
 16     402
 17    2731
 18     518
 19    2823
 20    2633
 21     334
 22     343
 23    3464
 24     381
 25    3141
 26     583
 27    3577
 28     486
 29    2136
 30    3604
 31     576
 32    3221
 33     724
 34    1161
 35    3578
 36    3278
 37    1254
 38    5954
 39    1290
 40     774
 41    1098
 42    1032
 43    1566
 44    3561
 45    3843
 46    2952
 47    1285
 48    2377
 49    1497
 50     714
 51     878
 52     328
 53     391
 54    1355
Name: count, dtype: int64


In [41]:
from sklearn.metrics import silhouette_score

# Hitung Silhouette Score (hanya untuk titik yang masuk cluster, bukan -1)
mask = df['cluster'] != -1
silhouette_avg = silhouette_score(features[mask], df['cluster'][mask])
print(f"Silhouette Score: {silhouette_avg}")

Silhouette Score: 0.3662224181768478


In [42]:
# Buat target
df['is_anomaly'] = df['cluster'].apply(lambda x: 1 if x == -1 else 0)

# Fitur dan target
X = df[['temp', 'out/in', 'hour']]
y = df['is_anomaly']

# Splitting
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [43]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV

# Model
logreg = LogisticRegression(random_state=42)

# Hyperparameter tuning
param_grid = {'C': [0.1, 1, 10], 'penalty': ['l1', 'l2'], 'solver': ['liblinear']}
grid_search = GridSearchCV(logreg, param_grid, cv=5, scoring='roc_auc')
grid_search.fit(X_train, y_train)

# Best model
best_logreg = grid_search.best_estimator_
print("Best Parameters:", grid_search.best_params_)

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\svm\_base.py:1249: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\svm\_base.py:1249: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.



Best Parameters: {'C': 10, 'penalty': 'l2', 'solver': 'liblinear'}


In [44]:
# Koefisien
coef = pd.DataFrame(best_logreg.coef_[0], index=X.columns, columns=['Coefficient'])
print("Koefisien Model:")
print(coef)

Koefisien Model:
        Coefficient
temp      -0.154804
out/in    -1.839357
hour       0.024943


In [45]:
import statsmodels.api as sm

# Tambahkan konstanta
X_train_sm = sm.add_constant(X_train)
logit_model = sm.Logit(y_train, X_train_sm)
result = logit_model.fit()
print(result.summary())

Optimization terminated successfully.
         Current function value: 0.000971
         Iterations 14
                           Logit Regression Results                           
Dep. Variable:             is_anomaly   No. Observations:                78084
Model:                          Logit   Df Residuals:                    78080
Method:                           MLE   Df Model:                            3
Date:                Fri, 06 Jun 2025   Pseudo R-squ.:                 0.06934
Time:                        22:23:56   Log-Likelihood:                -75.838
converged:                       True   LL-Null:                       -81.488
Covariance Type:            nonrobust   LLR p-value:                   0.01021
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         -7.5019      3.251     -2.308      0.021     -13.873      -1.131
temp          -0.0302      0

In [46]:
from sklearn.metrics import roc_auc_score

# Prediksi probabilitas
y_pred_prob = best_logreg.predict_proba(X_test)[:, 1]
roc_auc = roc_auc_score(y_test, y_pred_prob)
print(f"ROC-AUC Score: {roc_auc}")

ROC-AUC Score: 0.9998463114754099


In [47]:
from sklearn.metrics import confusion_matrix, classification_report

# Prediksi
y_pred = best_logreg.predict(X_test)

# Confusion matrix
cm = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:")
print(cm)

# Classification report
print("Classification Report:")
print(classification_report(y_test, y_pred))

Confusion Matrix:
[[19520     0]
 [    1     0]]
Classification Report:
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     19520
           1       0.00      0.00      0.00         1

    accuracy                           1.00     19521
   macro avg       0.50      0.50      0.50     19521
weighted avg       1.00      1.00      1.00     19521



C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` param

In [48]:
from sklearn.naive_bayes import GaussianNB

# Model
nb = GaussianNB()
nb.fit(X_train, y_train)

GaussianNB()

In [49]:
import numpy as np
# Ambil data uji pertama
sample = X_test.iloc[0]
print("Data Uji Pertama:")
print(sample)

# Probabilitas prior
prior_0 = nb.class_prior_[0]
prior_1 = nb.class_prior_[1]

# Probabilitas likelihood (Gaussian)
likelihood_0 = 1
likelihood_1 = 1
for i, feature in enumerate(X_test.columns):
    mean_0 = nb.theta_[0][i]
    mean_1 = nb.theta_[1][i]
    var_0 = nb.var_[0][i]
    var_1 = nb.var_[1][i]
    value = sample[feature]
    likelihood_0 *= (1 / (np.sqrt(2 * np.pi * var_0))) * np.exp(-((value - mean_0)**2) / (2 * var_0))
    likelihood_1 *= (1 / (np.sqrt(2 * np.pi * var_1))) * np.exp(-((value - mean_1)**2) / (2 * var_1))

# Probabilitas posterior
posterior_0 = prior_0 * likelihood_0
posterior_1 = prior_1 * likelihood_1
print(f"Posterior Probabilitas (Kelas 0): {posterior_0}")
print(f"Posterior Probabilitas (Kelas 1): {posterior_1}")

Data Uji Pertama:
temp      28
out/in     1
hour       0
Name: 63192, dtype: int64
Posterior Probabilitas (Kelas 0): 0.0003191794459869097
Posterior Probabilitas (Kelas 1): 1.0070101155253054e-10


In [50]:
# Varians fitur per kelas
print("Varians Fitur per Kelas:")
print(pd.DataFrame(nb.var_, columns=X.columns, index=['Normal', 'Anomaly']))

Varians Fitur per Kelas:
              temp    out/in       hour
Normal   32.492558  0.166101  42.759309
Anomaly  73.000000  0.187500  11.687500


In [51]:
# Prediksi
y_pred_nb = nb.predict(X_test)

# Confusion matrix
cm_nb = confusion_matrix(y_test, y_pred_nb)
print("Confusion Matrix (Naïve Bayes):")
print(cm_nb)

# Classification report
print("Classification Report (Naïve Bayes):")
print(classification_report(y_test, y_pred_nb))

# ROC-AUC
y_pred_prob_nb = nb.predict_proba(X_test)[:, 1]
roc_auc_nb = roc_auc_score(y_test, y_pred_prob_nb)
print(f"ROC-AUC Score (Naïve Bayes): {roc_auc_nb}")

Confusion Matrix (Naïve Bayes):
[[19520     0]
 [    1     0]]
Classification Report (Naïve Bayes):
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     19520
           1       0.00      0.00      0.00         1

    accuracy                           1.00     19521
   macro avg       0.50      0.50      0.50     19521
weighted avg       1.00      1.00      1.00     19521

ROC-AUC Score (Naïve Bayes): 0.9998463114754098


C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

C:\Users\Asus\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` param

In [58]:
# Langkah 1: Simpan model DBSCAN
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN
import joblib

# Load dataset secara lokal
try:
    df = pd.read_csv('IOT-temp.csv')
except FileNotFoundError:
    print("File IOT-temp.csv tidak ditemukan. Pastikan file ada di direktori yang sama.")
    exit()

# Preprocessing
df = df.drop_duplicates()
df['noted_date'] = pd.to_datetime(df['noted_date'], format='%d-%m-%Y %H:%M', errors='coerce')
df['hour'] = df['noted_date'].dt.hour
df = df.drop(columns=['id', 'room_id/id'])
df['temp'] = df['temp'].fillna(df['temp'].mean())
df['out/in'] = df['out/in'].map({'In': 0, 'Out': 1}).fillna(0)
df['hour'] = df['hour'].fillna(df['hour'].mode()[0])
scaler = StandardScaler()
df['temp_scaled'] = scaler.fit_transform(df[['temp']])

# Clustering dengan DBSCAN
dbscan = DBSCAN(eps=0.5, min_samples=5)
features = df[['temp_scaled', 'out/in', 'hour']]
df['cluster'] = dbscan.fit_predict(features)

# Simpan model DBSCAN
joblib.dump(dbscan, "dbscan_model.pkl")

# Langkah 2: Install dependensi
!pip install pyngrok -q
!pip install streamlit -q

# Langkah 3: Autentikasi Ngrok
# Ganti <your-authtoken> dengan token Ngrok Anda yang valid
!ngrok authtoken 2ww55iuAVykS1Gi7CYFWYKsXAFS_5i4MAWjQdcr9sGXSghAvN




[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: C:\Users\Asus\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip

[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: C:\Users\Asus\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


Authtoken saved to configuration file: C:\Users\Asus\AppData\Local/ngrok/ngrok.yml


In [62]:
# Langkah 4: Buat file app.py
import pandas as pd
import streamlit as st
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN
import plotly.express as px
import plotly.graph_objects as go
import joblib

# Set konfigurasi halaman Streamlit
st.set_page_config(
    page_title="Temperature Clustering Dashboard",
    page_icon="🌡️",
    layout="wide"
)

# Fungsi untuk membersihkan outlier
def clear_outlier(df, kolom_numerik, metode='iqr', threshold=1.5):
    Q1 = df[kolom_numerik].quantile(0.25)
    Q3 = df[kolom_numerik].quantile(0.75)
    IQR = Q3 - Q1
    batas_bawah = Q1 - threshold * IQR
    batas_atas = Q3 + threshold * IQR
    return df[(df[kolom_numerik] >= batas_bawah) & (df[kolom_numerik] <= batas_atas)]

# Fungsi untuk memuat data
@st.cache_data
def load_data():
    df = pd.read_csv('IOT-temp.csv')  # Dataset diakses secara lokal
    # Membersihkan outlier
    df = clear_outlier(df, 'temp')
    df.dropna(inplace=True)
    return df

# Fungsi untuk memuat model
@st.cache_resource
def load_model():
    return joblib.load('dbscan_model.pkl')

# Header
st.title("Temperature Clustering Dashboard (DBSCAN)")

# Overview Dashboard
st.markdown("""
## Selamat Datang di Dashboard Clustering Suhu

Dashboard ini menggunakan model DBSCAN untuk mengelompokkan data suhu berdasarkan kadar suhu, lokasi (In/Out), dan waktu.

### Dataset:
Dataset berisi informasi tentang suhu (`temp`), lokasi pengukuran (`out/in`), dan waktu (`noted_date`) dari sensor IoT pada periode Juli hingga Desember 2018.
""")

# Memuat data
try:
    df = load_data()
except FileNotFoundError:
    st.error("File IOT-temp.csv tidak ditemukan. Pastikan file ada di direktori yang sama.")
    st.stop()

# Statistik dasar
col1, col2, col3 = st.columns(3)
with col1:
    st.metric("Jumlah Data", df.shape[0])
with col2:
    st.metric("Pengukuran Dalam Ruangan", df[df['out/in'] == 'In'].shape[0])
with col3:
    st.metric("Pengukuran Luar Ruangan", df[df['out/in'] == 'Out'].shape[0])

# Preprocessing
df = df.drop_duplicates()
df['noted_date'] = pd.to_datetime(df['noted_date'], format='%d-%m-%Y %H:%M', errors='coerce')
df['hour'] = df['noted_date'].dt.hour
df = df.drop(columns=['id', 'room_id/id'])
df['temp'] = df['temp'].fillna(df['temp'].mean())
df['out/in'] = df['out/in'].map({'In': 0, 'Out': 1}).fillna(0)
df['hour'] = df['hour'].fillna(df['hour'].mode()[0])
scaler = StandardScaler()
df['temp_scaled'] = scaler.fit_transform(df[['temp']])

# Memuat model
model = load_model()

# Clustering menggunakan model yang dimuat
features = df[['temp_scaled', 'out/in', 'hour']]
df['cluster'] = model.fit_predict(features)

# Distribusi cluster
st.subheader("Distribusi Cluster")
fig_pie = px.pie(
    df,
    names='cluster',
    title='Distribusi Cluster DBSCAN',
    color_discrete_sequence=['#3498db', '#e74c3c', '#2ecc71', '#f1c40f'],
    labels={'cluster': 'Cluster'}
)
st.plotly_chart(fig_pie)

# Visualisasi clustering
st.markdown("---")
st.subheader("Hasil Clustering Suhu")

fig = px.scatter(
    df,
    x='noted_date',
    y='temp',
    color='cluster',
    title='Temperature Clustering (DBSCAN)',
    labels={'cluster': 'Cluster'},
    color_continuous_scale='Viridis'
)
fig.update_xaxes(
    tickformat="%b %d, %Y",
    tickangle=45,
    dtick=14*24*60*60*1000  # Interval 14 hari
)
st.plotly_chart(fig, use_container_width=True)

# Contoh data per cluster
st.subheader("Contoh Data per Cluster")
for cluster_label in sorted(df['cluster'].unique()):
    st.write(f"**Cluster {cluster_label}:**")
    st.write(df[df['cluster'] == cluster_label][['noted_date', 'temp', 'out/in']].head(3))

# Footer
st.markdown("---")

# Langkah 5: Jalankan Streamlit dan Ngrok
import subprocess
import time
from pyngrok import ngrok

# Jalankan Streamlit
process = subprocess.Popen("streamlit run app.py --server.port 8501", shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)

# Tunggu beberapa detik agar Streamlit berjalan
time.sleep(5)

# Cek log Streamlit
stdout, stderr = process.communicate(timeout=30)
print("Streamlit Log (stdout):")
print(stdout.decode())
print("Streamlit Log (stderr):")
print(stderr.decode())

# Buat URL publik dengan Ngrok
public_url = ngrok.connect(addr='8501')
print(f"Public URL: {public_url}")

2025-06-06 23:16:51.949 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.951 No runtime found, using MemoryCacheStorageManager
2025-06-06 23:16:51.955 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.956 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.958 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.959 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.991 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.993 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2025-06-06 23:16:51.993 Thread 'MainThread':

TimeoutExpired: Command 'streamlit run app.py --server.port 8501' timed out after 30 seconds